# Agrupando letras de músicas de Rock

Letras de músicas segundo o vagalume.com.br, coletadas por Anderson Neisse e [disponíveis no kaggle](https://www.kaggle.com/neisse/scrapped-lyrics-from-6-genres/data).

Os dados originais foram tratados para diminuir duplicações e diminuir o tamanho do arquivo. Os resultados (e outros recortes dos dados de letras) estão [nesse repo](https://github.com/nazareno/palavras-nas-letras).

In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
from sklearn import preprocessing, decomposition, model_selection, metrics, pipeline
from sklearn.cluster import KMeans
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
import re

[nltk_data] Downloading package stopwords to /home/mateus/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [4]:
rock_lyrics = pd.read_csv('https://raw.githubusercontent.com/nazareno/palavras-nas-letras/master/letras-ptbr-rock-grande.csv')

#### Observações iniciais
Vamos começar realizando algumas observações superficiais do Dataframe, a partir dos métodos sample(), info() e value_counts() de artistas.

In [5]:
rock_lyrics.sample(10)

SName  \
2574                  Além Do Horizonte   
7176                              A Lua   
2550  Pra Quando Você Se Lembrar de Mim   
2972               A Marcha Dos Infames   
2448                           Digitais   
5085                   Vida à Prestação   
3285                              Graal   
5791              Esc (Caverna digital)   
5909                  Eu E A Felicidade   
2389            Não Consigo Me Entreter   

                                                  Lyric            Artist  \
2574  Além do horizonte existe um lugar. Bonito e tr...        Jota Quest   
7176  A lua que faz brilhar o teu olhar, meu amor. E...        Jota Quest   
2550  Quando você, se lembrar, de mim. Pensa que tud...        Jota Quest   
2972  Aqueles que não são. E que jamais serão. Abusa...             Lobão   
2448  Eu tava aqui tentando não pensar no seu sorris...  Isabella Taviani   
5085  Acorda cedo. Café na mesa. Toma seu carro e se...       Raul Seixas   
3285  É necessário descobrir. O que é que Jesus Cris...       Lulu Santos   
5791  Ah, se eu pudesse.... Tiraria você de mim. O q...           Scalene   
5909  E afinal ela quer me entregar. Ou não quer?. U...             Skank   
2389  Não acho graça nos problemas da tv,. não acho ...              Ira!   

      Songs  Popularity Genre  \
2574    154        13.3  Rock   
7176    154        13.3  Rock   
2550    154        13.3  Rock   
2972    112         1.3  Rock   
2448     97         1.3  Rock   
5085    215        14.0  Rock   
3285    271        10.0  Rock   
5791     73         0.8  Rock   
5909    139        12.3  Rock   
2389    140         3.4  Rock   

                                                 Genres  
2574  Pop/Rock; Pop; Rock; Romântico; Funk; Black Mu...  
7176  Pop/Rock; Pop; Rock; Romântico; Funk; Black Mu...  
2550  Pop/Rock; Pop; Rock; Romântico; Funk; Black Mu...  
2972  Rock; MPB; Rock Alternativo; Punk Rock; Psicod...  
2448  MPB; Rock; Romântico; Pop/Rock; Pop; Axé; Clás...  
5085  Rock; Pop/Rock; MPB; Rock Alternativo; Clássic...  
3285  Pop/Rock; Rock; Pop; MPB; Dance; Electronica; ...  
5791  Rock Alternativo; Rock; Pop/Rock; Hardcore; Pu...  
5909  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Ro...  
2389                                               Rock

In [6]:
rock_lyrics.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7680 entries, 0 to 7679
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   SName       7680 non-null   object 
 1   Lyric       7680 non-null   object 
 2   Artist      7680 non-null   object 
 3   Songs       7680 non-null   int64  
 4   Popularity  7680 non-null   float64
 5   Genre       7680 non-null   object 
 6   Genres      7680 non-null   object 
dtypes: float64(1), int64(1), object(5)
memory usage: 420.1+ KB


In [7]:
rock_lyrics['Artist'].value_counts()[0:20]

Lulu Santos                462
Engenheiros do Hawaii      402
Jota Quest                 296
Skank                      290
Rita Lee                   282
Erasmo Carlos              236
Cássia Eller               226
Titãs                      209
Charlie Brown Jr           198
Raul Seixas                196
Capital Inicial            195
Biquini Cavadão            184
Os Paralamas do Sucesso    181
Barão Vermelho             164
Velhas Virgens             156
Fresno                     153
Blitz                      150
Pato Fu                    146
Ira!                       142
Rosa de Saron              137
Name: Artist, dtype: int64

#### Pré-processamento
Faremos o pré-processamento dos textos das letras a partir da exclusão de caracteres especiais

In [14]:
stop_words = set(stopwords.words("portuguese"))
print(len(stop_words))

204


In [12]:
rock_lyrics_c = []
rock_songs_titles = []
rock_titles_lyrics = []

for i in range(len(rock_lyrics.Lyric)):
    lyric = rock_lyrics['Lyric'][i]
    title = rock_lyrics['SName'][i]

    #remove special characters and digits
    lyric  = re.sub("(\\d|\\W)+|\w*\d\w*"," ",lyric )
    lyric = ' '.join(s for s in lyric.split() if (not any(c.isdigit() for c in s)) and len(s) > 2)
    rock_lyrics_c.append(lyric)
    rock_songs_titles.append(title)
    rock_titles_lyrics.append("{title} {lyric}".format(title = title, lyric = lyric))

rock_titles_lyrics[5:7]

['Meu Caminho Saudade Espero que logo logo vai passar Vontade Hoje quero matar com você Sempre que puder voltarei aqui Sempre que puder quero ver sorrir Felicidade vale tiver alguém pra dividir vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração levo comigo aprendi usar solidão vivo bem comigo mesmo então Respeito com liberdade Onde estiver seja bem vinda agora você quiser Sempre que puder voltarei aqui Sempre que puder quero ver sorrir Felicidade vale tiver alguém pra dividir vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração levo comigo vou levar pra ver sol pra ver mar Andar meu caminho levo emoção pra acelerar meu coração Não quero estar sozinho vou levar pra ver sol pra ver mar Andar m

#### Criando vetores TF-IDF

In [15]:
#TF-IDF vectorizer
tfv_lyrics = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )

tfv_titles = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )

tfv_titles_lyrics = TfidfVectorizer(
        min_df = 10,
        max_df = 0.5,
        max_features = None,
        stop_words = stop_words, 
        ngram_range = (1,3)
  )



#transform
vec_lyrics = tfv_lyrics.fit_transform(rock_lyrics_c)
vec_titles = tfv_titles.fit_transform(rock_songs_titles)
vec_titles_lyrics = tfv_titles_lyrics.fit_transform(rock_titles_lyrics)

#returns a list of words.
lyrics_words = tfv_lyrics.get_feature_names()
titles_words = tfv_titles.get_feature_names()
tl_words = tfv_titles_lyrics.get_feature_names()

print(len(lyrics_words), len(titles_words), len(tl_words))

8525 226 8632


/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


### Escolhendo o valor de K
Para escolher o valor de K, usaremos o método do 'cotovelo': escolheremos o valor a partir do qual não haverá ganho substancial de coesão dos grupos com um valor de K maior.


In [24]:
from sklearn.cluster import MiniBatchKMeans

# k é o número de clusters, e ssd é nosso parâmetro de 'qualidade', calculado a partir das somas das distâncias quadráticas entre cada ponto e o centroide de seu respectivo grupo
# Considerando que os dados
qualidade_lyrics = pd.DataFrame(columns = ['k', 'ssd'])
qualidade_titles = pd.DataFrame(columns = ['k', 'ssd'])
qualidade_tl = pd.DataFrame(columns = ['k', 'ssd'])

for k in range(1, 17):
  kmeans_l = MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048, random_state=20)
  kmeans_l.fit(vec_lyrics)
  qualidade_lyrics = qualidade_lyrics.append({'k': k, 'ssd' : kmeans_l.inertia_}, ignore_index=True)

  kmeans_t = KMeans(n_clusters=k, random_state=0)
  kmeans_t.fit(vec_titles)
  qualidade_titles = qualidade_titles.append({'k': k, 'ssd' : kmeans_t.inertia_}, ignore_index=True)

  kmeans_tl = MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048, random_state=20)
  kmeans_tl.fit(vec_titles_lyrics)
  qualidade_tl = qualidade_tl.append({'k': k, 'ssd' : kmeans_tl.inertia_}, ignore_index=True)


In [22]:
alt.Chart(qualidade_lyrics).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

In [25]:
alt.Chart(qualidade_titles).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

In [26]:
alt.Chart(qualidade_tl).mark_line(
    point=True
).encode(
    x = 'k',
    y = alt.Y('ssd', scale = alt.Scale(zero=False))
)

alt.Chart(...)

O valor de K escolhido para cada grupo será 8.

### Agrupando com o valor de K escolhido

In [27]:
kmeans_l = MiniBatchKMeans(n_clusters=8, init_size=1024, batch_size=2048, random_state=20)
kmeans_l.fit(vec_lyrics)
labels_l = kmeans_l.predict(vec_lyrics)

lyrics_ag = rock_lyrics.assign(grupo = labels_l)


lyrics_ag.sample(10)


SName                                              Lyric  \
1803     A Semana Inteira  A semana inteira 1970. Erasmo Carlos - Roberto...   
1240     Tarde de Outubro  Peguei minhas coisas fui embora. Não queria ma...   
1618        Arame Farpado  Seria engraçado. Se não fosse triste. acesso n...   
3270       Éros E Tanatos  Sou mais meu Éros do que o seu Tanatos. seu Ta...   
6371              Zoraide  Já não sei se te quero, acho que não quero,. M...   
3134               Morena  É morena tá tudo bem. Sereno é quem tem. A paz...   
4194  O Rouxinol E A Rosa  Sob o céu frio e cinza. Um impasse e poucas op...   
925            Vai à Luta  Eu li teu nome num cartaz. Com letras de néon ...   
2852       Melhor Pra Mim  Olhando as estrelas. Nada no espaço. Fica para...   
4310    Crédito ou Débito  Não vai haver saída. Você vai ter que se expli...   

                       Artist  Songs  Popularity Genre  \
1803            Erasmo Carlos    225         2.3  Rock   
1240                   CPM 22    114         3.2  Rock   
1618    Engenheiros do Hawaii    193        11.9  Rock   
3270              Lulu Santos    271        10.0  Rock   
6371          Ultraje A Rigor     90         2.1  Rock   
3134             Los Hermanos     80         5.5  Rock   
4194  Os Paralamas do Sucesso    224         7.0  Rock   
925                    Cazuza    123         9.6  Rock   
2852                    Leoni     91         2.0  Rock   
4310                  Pato Fu    146         1.4  Rock   

                                                 Genres  grupo  
1803  Rock; Jovem Guarda; Romântico; MPB; Soul Music...      5  
1240  Hardcore; Punk Rock; Rock; Pop/Rock; Hard Rock...      7  
1618  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Se...      1  
3270  Pop/Rock; Rock; Pop; MPB; Dance; Electronica; ...      3  
6371  Rock; Pop/Rock; Rock Alternativo; Punk Rock; M...      6  
3134  Rock Alternativo; Rock; MPB; Romântico; Indie;...      0  
4194                                               Rock      1  
925   Pop/Rock; MPB; Rock; Romântico; Rock Alternati...      5  
2852        MPB; Rock; Romântico; Pop/Rock; Pop; Reggae      1  
4310  Rock; Pop/Rock; Pop; MPB; Indie; Rock Alternat...      3

In [34]:
kmeans_t =  KMeans(n_clusters=5, random_state=0)
kmeans_t.fit(vec_titles)
labels_t = kmeans_t.predict(vec_titles)

titles_ag = rock_lyrics.assign(grupo = labels_t)


titles_ag.sample(10)

SName  \
4139        El Amor (el Amor Despues Del Amor)   
6704  Colorindo o Visual (Part. Neto Trindade)   
6869                          Mapa do Meu Nada   
3514                   Eu Não Gosto de Ninguém   
4669                      Malditos Cromossomos   
6811     Meu Mundo Ficaria Completo (Com Você)   
6522                A Boca, A Buceta E A Bunda   
887                       Incapacidade de Amar   
7609                           Garota Nacional   
951                     A Banca (acústico MTV)   

                                                  Lyric  \
4139  Meu amor, depois de te amar talvez. Seja como ...   
6704  É a viajem de enxergar colorido. E não importa...   
6869  Você é dedos que eu te quero, tocou. Você é be...   
3514  Não me faça nem um favor.. Não espere nada de ...   
4669  Todas as características. Explícitas ou escond...   
6811  Não é porque eu sujei a roupa bem agora que eu...   
6522  A Boca, a buceta e a bunda. Começaram uma disc...   
887   Vai embora não, fica mais. Homem nenhum no mun...   
7609  Aqui nesse mundinho fechado ela é incrível. Co...   
951   Taê, agora é meu eu vou taca e roda, roda. E c...   

                       Artist  Songs  Popularity Genre  \
4139  Os Paralamas do Sucesso    224         7.0  Rock   
6704                 Ventania     35         1.3  Rock   
6869             Cássia Eller    141         7.5  Rock   
3514                  Matanza     95         1.3  Rock   
4669                    Pitty     98         8.1  Rock   
6811             Cássia Eller    141         7.5  Rock   
6522           Velhas Virgens    137         2.4  Rock   
887                    Cazuza    123         9.6  Rock   
7609                    Skank    139        12.3  Rock   
951          Charlie Brown Jr    208        25.7  Rock   

                                                 Genres  grupo  
4139                                               Rock      2  
6704  Reggae; Rock; Rock Alternativo; Ska; Reggaeton...      1  
6869  Rock; MPB; Pop/Rock; Pop; Romântico; Samba; Co...      1  
3514  Hardcore; Rock; Hard Rock; Heavy Metal; Countr...      1  
4669  Rock Alternativo; Rock; Pop/Rock; Punk Rock; H...      1  
6811  Rock; MPB; Pop/Rock; Pop; Romântico; Samba; Co...      1  
6522  Rock; Blues; Punk Rock; Hard Rock; Rock Altern...      1  
887   Pop/Rock; MPB; Rock; Romântico; Rock Alternati...      1  
7609  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Ro...      1  
951   Pop/Rock; Rap; Rock; Reggae; Rock Alternativo;...      1

In [35]:
kmeans_tl = MiniBatchKMeans(n_clusters=8, init_size=1024, batch_size=2048, random_state=20)
kmeans_tl.fit(vec_titles_lyrics)
labels_tl = kmeans_tl.predict(vec_titles_lyrics)

tl_ag = rock_lyrics.assign(grupo = labels_tl)


tl_ag.sample(10)

SName  \
5482          Foi Bom Esperar   
1530              Tênis Roque   
4786     Esporrei Na Manivela   
1985         Sodoma E Gomorra   
1790             Novo Sentido   
883              Guerra Civil   
6833                 Ausência   
4921       A Pedra do Gênesis   
5128               Duas Vezes   
7578  Balada Pra João E Joana   

                                                  Lyric            Artist  \
5482  O mesmo trem vai passar noutra cidade. Faz min...             Rodox   
1530  Peguei meu tênis e fui atrás do meu melhor. Ho...        Detonautas   
4786  Entrei no trem, esporrei na manivela. Cobrador...         Raimundos   
1985  Sodoma e Gomorra. Roberto Carlos - Erasmo Carl...     Erasmo Carlos   
1790  Deixe estar, meu amor. Que eu não preciso de l...     Erasmo Carlos   
883   Para o meio da rua, me atropelei de mais. Algu...            Cazuza   
6833  Tu lembras?. Da rua tão estreita estrada tão a...      Cássia Eller   
4921  No fundo do oceano existe um baú. Que guarda o...       Raul Seixas   
5128  Um coração partido comete loucuras. Transforma...  Reação Em Cadeia   
7578  Então os dois se acharam na escuridão. Ela com...             Skank   

      Songs  Popularity Genre  \
5482     29         0.7  Rock   
1530    120         2.0  Rock   
4786    121         4.2  Rock   
1985    225         2.3  Rock   
1790    225         2.3  Rock   
883     123         9.6  Rock   
6833    141         7.5  Rock   
4921    215        14.0  Rock   
5128     84         0.8  Rock   
7578    139        12.3  Rock   

                                                 Genres  grupo  
5482  Rock; Gospel/Religioso; Hardcore; Punk Rock; P...      4  
1530                                               Rock      2  
4786  Punk Rock; Hardcore; Rock; Pop/Rock; Hard Rock...      5  
1985  Rock; Jovem Guarda; Romântico; MPB; Soul Music...      2  
1790  Rock; Jovem Guarda; Romântico; MPB; Soul Music...      0  
883   Pop/Rock; MPB; Rock; Romântico; Rock Alternati...      5  
6833  Rock; MPB; Pop/Rock; Pop; Romântico; Samba; Co...      5  
4921  Rock; Pop/Rock; MPB; Rock Alternativo; Clássic...      5  
5128  Pop/Rock; Rock; Rock Alternativo; Romântico; G...      0  
7578  Pop/Rock; Rock; Pop; Rock Alternativo; MPB; Ro...      1

### Interpretando os grupos
Interpretaremos o grupo a partir da observação das palavras mais comuns de cada grupo, dos artistas mais presentes em cada grupo e da visualização dos grupos, com uma técnica de redução de dimensionalidade.

Começaremos a análise com as letras das músicas

In [41]:
# Vamos olhar a quantidade de músicas em cada grupo
lyrics_ag['grupo'].value_counts()


5    2725
1     897
3     894
7     755
0     744
6     708
2     674
4     283
Name: grupo, dtype: int64

In [39]:
# Olharemos, agora, as palavras mais comuns em cada grupo
lyrics_common_words = kmeans_l.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(lyrics_common_words):
    print(str(num) + ' : ' + ', '.join(lyrics_words[word] for word in centroid))



0 : amor, mim, coração, tudo, ser, vem, dor, vou, vai, vida, amar, bem, assim, sei
1 : gente, sempre, sol, vem, quer, faz, nada, tudo, dia, vida, luz, ninguém, tempo, noite
2 : vamos, mundo, hoje, todo, dia, todo mundo, tudo, todos, vai, ser, vida, gente, tempo, amo
3 : vou, vai, tudo, sei, mim, aqui, tempo, agora, onde, ser, ficar, dia, vez, ver
4 : vida, toda, vida vida, tudo, gente, viver, ter, ser, tempo, mundo, vai, sinto, dia, agora
5 : vai, bem, tão, tudo, ser, mim, deus, aqui, ninguém, assim, faz, pode, tempo, mal
6 : quero, ser, ver, vai, tudo, vou, mim, sei, bem, quero ver, sempre, nada, quero ser, nunca
7 : sei, dizer, nada, coisas, tudo, mim, tempo, preciso, assim, viver, aqui, ser, agora, nunca


0 -> grupo dos amantes (os que cantam sobre um amor ardente, que existe ou não existe mais)
1 -> grupo dos esperançosos e dos desesperançosos (pensamentos bons ou ruins sobre futuro)
2 -> grupo dos festeiros (muitas menções a festas, dias de semana e acordar sentindo o que se sente em uma sexta)
3 -> grupo dos "estou te esperando" (amores escondidos, ou amores passados que ainda perduram no coração de alguém)
4 -> grupo dos pensantes sobre a vida (muitas menções a vida e ao ato de viver)
5 -> grupo dos invocados (menções de inferno, sangue, alma, Deus e palavrões)
6 -> 
7 -> grupo dos revolucionários

In [76]:
pd.options.display.max_colwidth = 100
lyrics_ag.query('grupo == 6')[['SName', 'Lyric', 'Artist']].sample(10)

SName  \
7589                 Do Ben   
1823           Celebridades   
4274    Ando Meio Desligado   
6857         Fiz O Que Pude   
1068  Pontes Indestrutíveis   
3388          Tudo Com Você   
5122    Canção da Despedida   
379        Meus Dois Amores   
387         No mundo da Lua   
5566       Caminho de Emaús   

                                                                                                    Lyric  \
7589  Sua mão direita vale ouro. Que trouxe o novo som. Pra dividir com os outros. Simpatia gera simpa...   
1823  Pôs um piercing no umbigo,. tatuou o cupido no bumbum,. todo mundo é seu amigo. eu apenas sou ma...   
4274  Ando meio desligado... Eu nem sinto meus pés no chão. Olho e não vejo nada. Eu só penso se você ...   
6857  Eu não vou mais chorar. Eu fiz o que pude. Não paro de pensar. A tua ausência que me ilude. Não ...   
1068  Buscando um novo rumo que faça sentido nesse mundo louco com o coração partido, eu. Tomo cuidado...   
3388  Quero te conquistar. Um pouco mais e mais. A cada dia. Satisfazer tua vontade. Também me sacia. ...   
5122  Algo se encantou. Foi um sentimento que brilhou. Não dá pra negar. Uma vida que foi minha. Uma v...   
379   minha égua é bem ligeira. ela é a campeã. nada é mais veloz que as suas pernas musculosas. basta...   
387   Quando os astronautas foram a Lua. Que coincidência, eu também estava lá. Fugindo de casa, do ba...   
5566  Tarde cinza em queixas. Vivendo decepção. Testemunhos confusão. Espero libertação. Em meio a tan...   

                Artist  
7589             Skank  
1823     Erasmo Carlos  
4274           Pato Fu  
6857      Cássia Eller  
1068  Charlie Brown Jr  
3388       Lulu Santos  
5122  Reação Em Cadeia  
379    Biquini Cavadão  
387    Biquini Cavadão  
5566     Rosa de Saron

In [46]:
for g in range(0, 7):
  print('\n-----\nGRUPO {}:'.format(g))
  print(lyrics_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Jota Quest                 54
Lulu Santos                40
Erasmo Carlos              38
Skank                      36
Rita Lee                   33
Isabella Taviani           31
Los Hermanos               30
Rosa de Saron              29
Cássia Eller               28
Os Paralamas do Sucesso    26
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Engenheiros do Hawaii      90
Lulu Santos                66
Jota Quest                 52
Skank                      46
Rita Lee                   33
Os Paralamas do Sucesso    33
Capital Inicial            27
Erasmo Carlos              26
Velhas Virgens             26
Barão Vermelho             25
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Engenheiros do Hawaii    68
Lulu Santos              50
Jota Quest               42
Capital Inicial          26
Legião Urbana            24
Charlie Brown Jr         22
Blitz                    22
Skank                    22
Cássia Eller             20
Barão Vermelho           20
Name: 

In [48]:
from sklearn.manifold import TSNE

lyrics_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_lyrics)

/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.001s...
[t-SNE] Computed neighbors for 7680 samples in 2.276s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.542048
[t-SNE] KL divergence after 250 iterations with early exaggeration: 128.586304
[t-SNE] KL divergence after 1000 iterations: 3.790422


In [60]:
lyrics_ag = lyrics_ag.assign(tsne1 = lyrics_embedded[:,0], tsne2 = lyrics_embedded[:,1])

alt.Chart(lyrics_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)

Agora, faremos a análise a partir dos títulos das músicas

In [80]:
titles_ag['grupo'].value_counts()

1    7336
2     179
3     104
4      50
0      11
Name: grupo, dtype: int64

In [81]:
titles_common_words = kmeans_t.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(titles_common_words):
    print(str(num) + ' : ' + ', '.join(titles_words[word] for word in centroid))

0 : remix, luz, tudo, sincero, pra ser, ser, coisa, país, novo, pra, faz, feira, feat, feliz
1 : pra, part, mundo, vida, dia, tempo, mim, sol, vou, noite, nada, coração, vai, ser
2 : amor, apenas, grande, maior, daqui, vida, todo, balada, quente, mim, canção, part, onde, paz
3 : tudo, bem, vai, azul, lembrar, faz, ficar, meio, amor, fim, ser, sol, vida, longe
4 : homem, bom, coração, velho, demais, ii, mulher, rua, mar, deus, verdade, quero, ser, lembrar


In [82]:
for g in range(0, 7):
  print('\n-----\nGRUPO {}:'.format(g))
  print(titles_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Strike                   3
Engenheiros do Hawaii    2
Jota Quest               2
Legião Urbana            1
Titãs                    1
Charlie Brown Jr         1
Capital Inicial          1
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Lulu Santos              432
Engenheiros do Hawaii    388
Skank                    278
Jota Quest               272
Rita Lee                 271
Erasmo Carlos            226
Cássia Eller             222
Titãs                    198
Raul Seixas              193
Charlie Brown Jr         192
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Lulu Santos                14
Blitz                      12
Jota Quest                 12
Leoni                      12
Barão Vermelho              9
Rita Lee                    8
PG                          8
Ira!                        7
Os Paralamas do Sucesso     6
Reação Em Cadeia            6
Name: Artist, dtype: int64
-----

-----
GRUPO 3:
Lulu Santos         16
Jota Quest           8
Frejat      

In [83]:
from sklearn.manifold import TSNE

titles_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_titles)

/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.000s...
[t-SNE] Computed neighbors for 7680 samples in 0.788s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.000000
[t-SNE] KL divergence after 250 iterations with early exaggeration: 99.359726
[t-SNE] KL divergence after 1000 iterations: 2.334664


In [86]:
titles_ag = titles_ag.assign(tsne1 = titles_embedded[:,0], tsne2 = titles_embedded[:,1])

alt.Chart(titles_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)

Finalmente, faremos a análise a partir dos títulos concatenados com as letras

In [87]:
tl_ag['grupo'].value_counts()

5    2596
1    1161
3     926
2     794
0     707
4     659
6     603
7     234
Name: grupo, dtype: int64

In [88]:
tl_common_words = kmeans_tl.cluster_centers_.argsort()[:,-1:-15:-1]
for num, centroid in enumerate(tl_common_words):
    print(str(num) + ' : ' + ', '.join(tl_words[word] for word in centroid))


0 : amor, coração, tudo, vida, ser, vou, vem, amar, vai, dor, mim, mundo, dia, bem
1 : gente, sempre, vida, dia, sol, nada, faz, quer, tudo, noite, vem, tempo, medo, vai
2 : quero, vamos, ver, hoje, ser, dia, sei, tudo, vida, bem, vai, quero ver, amo, nada
3 : vou, vai, sei, tempo, tudo, aqui, agora, dizer, vez, onde, ficar, quero, ser, dia
4 : mim, tudo, pra mim, assim, sei, aqui, posso, vai, fim, ser, bem, vou, quero, sempre
5 : vai, tão, ser, bem, onde, tudo, aqui, vida, tempo, assim, nada, pode, sei, mal
6 : ninguém, todo, mundo, todo mundo, sabe, tudo, vai, dia, bem, vida, the, ser, gente, faz
7 : deus, senhor, jesus, rei, homem, cristo, coração, amor, aleluia, glória, vida, deus deus, viver, terra


In [89]:
pd.options.display.max_colwidth = 100
tl_ag.query('grupo == 4')[['SName', 'Lyric', 'Artist']].sample(10)

SName  \
7316                               Tudo Azul   
2283              Sentado À Beira do Caminho   
6320                    Querem Acabar Comigo   
1859                Enforcadinho Por Brigite   
2794                       Meninos e Meninas   
1876              Gosto do Tudo Das Mulheres   
616                                   Giulia   
5911                                    Fica   
2230  Hoje Sou Trovão (Part. Caetano Veloso)   
532                             O Passageiro   

                                                                                                    Lyric  \
7316  Tudo azul, todo mundo nu. No Brasil sol de norte a sul. Tudo bem, tudo zen, meu bem. Tudo sem fo...   
2283  Eu não posso mais ficar aqui a esperar. Que um dia, de repente, você volte para mim. Vejo caminh...   
6320  Querem acabar comigo. Nem eu mesmo sei porque. Enquanto eu tiver você aqui. Ninguém poderá me de...   
1859  Bis (brigite, brigite não faça assim. (brigite, brigite tem dó de mim. todo dia, toda noite, min...   
2794  Quero me encontrar, mas não sei onde estou. Vem comigo procurar algum lugar mais calmo. Longe de...   
1876  Gosto do tudo nas mulheres. Minúcia que provoca. Uma interrogação. Centro cativante do universo....   
616   Agora eu já posso morrer em paz. Eu tenho um milhão de contas a pagar. Mas agora tanto faz. Seu ...   
5911  Se você vai trabalhar. E me deixar, que pena!. Eu corro risco tão sozinho. Nessa ogiva azul imen...   
2230  Eu me escondi nas encostas pra enxergar. Tudo que eu perdi por medo de tentar. Eu já menti até o...   
532   Eu sou o passageiro. Eu rodo sem parar. Eu rodo pelos subúrbios escuros. Eu vejo estrelas saindo...   

               Artist  
7316      Lulu Santos  
2283           Fresno  
6320            Titãs  
1859    Erasmo Carlos  
2794    Legião Urbana  
1876    Erasmo Carlos  
616   Capital Inicial  
5911            Skank  
2230           Fresno  
532   Capital Inicial

In [90]:
for g in range(0, 7):
  print('\n-----\nGRUPO {}:'.format(g))
  print(tl_ag.query('grupo ==  {}'.format(g))['Artist'].value_counts()[0:10])
  print('-----')


-----
GRUPO 0:
Jota Quest                 56
Skank                      36
Lulu Santos                36
Erasmo Carlos              33
Rita Lee                   31
Cássia Eller               28
Isabella Taviani           27
Los Hermanos               26
Os Paralamas do Sucesso    26
Barão Vermelho             26
Name: Artist, dtype: int64
-----

-----
GRUPO 1:
Engenheiros do Hawaii      114
Lulu Santos                 94
Jota Quest                  64
Os Paralamas do Sucesso     45
Skank                       42
Biquini Cavadão             42
Rita Lee                    41
Capital Inicial             38
Erasmo Carlos               36
Raul Seixas                 35
Name: Artist, dtype: int64
-----

-----
GRUPO 2:
Lulu Santos              50
Cássia Eller             42
Engenheiros do Hawaii    34
Erasmo Carlos            27
Skank                    26
Charlie Brown Jr         26
Rita Lee                 24
Legião Urbana            23
Detonautas               22
Raul Seixas             

In [93]:
tl_embedded = TSNE(n_components=2, verbose=1).fit_transform(vec_titles_lyrics)

/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/mateus/anaconda3/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 7680 samples in 0.001s...
[t-SNE] Computed neighbors for 7680 samples in 2.417s...
[t-SNE] Computed conditional probabilities for sample 1000 / 7680
[t-SNE] Computed conditional probabilities for sample 2000 / 7680
[t-SNE] Computed conditional probabilities for sample 3000 / 7680
[t-SNE] Computed conditional probabilities for sample 4000 / 7680
[t-SNE] Computed conditional probabilities for sample 5000 / 7680
[t-SNE] Computed conditional probabilities for sample 6000 / 7680
[t-SNE] Computed conditional probabilities for sample 7000 / 7680
[t-SNE] Computed conditional probabilities for sample 7680 / 7680
[t-SNE] Mean sigma: 0.542122
[t-SNE] KL divergence after 250 iterations with early exaggeration: 123.650726
[t-SNE] KL divergence after 1000 iterations: 3.822103


In [94]:
tl_ag = tl_ag.assign(tsne1 = tl_embedded[:,0], tsne2 = tl_embedded[:,1])

alt.Chart(tl_ag.sample(1000)).mark_circle(
    opacity = .7,
    size = 30
).encode(
    x = 'tsne1',
    y = 'tsne2', 
    color = 'grupo:N',
    tooltip = ['Artist', 'SName']
).interactive()

alt.Chart(...)